In [1]:
import csv
import collections
import numpy as np
import pandas as pd
from autogluon.tabular import TabularDataset, TabularPredictor
from autogluon.common.utils.utils import setup_outputdir
from autogluon.core.utils.loaders import load_pkl
from autogluon.core.utils.savers import save_pkl
import os.path
from sklearn.model_selection import train_test_split
import time
import matplotlib.pyplot as plt
import seaborn as sns
from random import sample

In [2]:
class MultilabelPredictor():
    """ Tabular Predictor for predicting multiple columns in table.
        Creates multiple TabularPredictor objects which you can also use individually.
        You can access the TabularPredictor for a particular label via: `multilabel_predictor.get_predictor(label_i)`

        Parameters
        ----------
        labels : List[str]
            The ith element of this list is the column (i.e. `label`) predicted by the ith TabularPredictor stored in this object.
        path : str, default = None
            Path to directory where models and intermediate outputs should be saved.
            If unspecified, a time-stamped folder called "AutogluonModels/ag-[TIMESTAMP]" will be created in the working directory to store all models.
            Note: To call `fit()` twice and save all results of each fit, you must specify different `path` locations or don't specify `path` at all.
            Otherwise files from first `fit()` will be overwritten by second `fit()`.
            Caution: when predicting many labels, this directory may grow large as it needs to store many TabularPredictors.
        problem_types : List[str], default = None
            The ith element is the `problem_type` for the ith TabularPredictor stored in this object.
        eval_metrics : List[str], default = None
            The ith element is the `eval_metric` for the ith TabularPredictor stored in this object.
        consider_labels_correlation : bool, default = True
            Whether the predictions of multiple labels should account for label correlations or predict each label independently of the others.
            If True, the ordering of `labels` may affect resulting accuracy as each label is predicted conditional on the previous labels appearing earlier in this list (i.e. in an auto-regressive fashion).
            Set to False if during inference you may want to individually use just the ith TabularPredictor without predicting all the other labels.
        kwargs :
            Arguments passed into the initialization of each TabularPredictor.

    """

    multi_predictor_file = 'multilabel_predictor.pkl'

    def __init__(self, labels, path=None, problem_types=None, eval_metrics=None, consider_labels_correlation=False, **kwargs):
        if (problem_types is not None) and (len(problem_types) != len(labels)):
            raise ValueError("If provided, `problem_types` must have same length as `labels`")
        if (eval_metrics is not None) and (len(eval_metrics) != len(labels)):
            raise ValueError("If provided, `eval_metrics` must have same length as `labels`")
        self.path = setup_outputdir(path, warn_if_exist=False)
        self.labels = labels
        self.consider_labels_correlation = consider_labels_correlation
        self.predictors = {}  # key = label, value = TabularPredictor or str path to the TabularPredictor for this label
        if eval_metrics is None:
            self.eval_metrics = {}
        else:
            self.eval_metrics = {labels[i] : eval_metrics[i] for i in range(len(labels))}
        problem_type = None
        eval_metric = None
        for i in range(len(labels)):
            label = labels[i]
            path_i = self.path + "Predictor_" + label
            if problem_types is not None:
                problem_type = problem_types[i]
            if eval_metrics is not None:
                eval_metric = eval_metrics[i]
            self.predictors[label] = TabularPredictor(label=label, problem_type=problem_type, eval_metric=eval_metric, path=path_i, **kwargs)

    def fit(self, train_data, tuning_data=None, final = False, **kwargs):
        """ Fits a separate TabularPredictor to predict each of the labels.

            Parameters
            ----------
            train_data, tuning_data : str or autogluon.tabular.TabularDataset or pd.DataFrame
                See documentation for `TabularPredictor.fit()`.
            kwargs :
                Arguments passed into the `fit()` call for each TabularPredictor.
        """
        if isinstance(train_data, str):
            train_data = TabularDataset(train_data)
        if tuning_data is not None and isinstance(tuning_data, str):
            tuning_data = TabularDataset(tuning_data)
        train_data_og = train_data.copy()
        if tuning_data is not None:
            tuning_data_og = tuning_data.copy()
        else:
            tuning_data_og = None
        save_metrics = len(self.eval_metrics) == 0
        start = time.time()
        for i in range(len(self.labels)):
            label = self.labels[i]
            predictor = self.get_predictor(label)
            if not self.consider_labels_correlation:
                labels_to_drop = [l for l in self.labels if l != label]
            else:
                labels_to_drop = [self.labels[j] for j in range(i+1, len(self.labels))]
            train_data = train_data_og.drop(labels_to_drop, axis=1)
            if tuning_data is not None:
                tuning_data = tuning_data_og.drop(labels_to_drop, axis=1)
            print(f"Fitting TabularPredictor for label: {label} ...{i / len(self.labels) * 100}%")
            print(f"{(time.time() - start) / 60} minutes")
            if (final):
                predictor.fit(train_data=train_data[train_data[label] > float('-inf')]
                              , tuning_data = tuning_data
                              ,presets = 'best_quality'
                              ,num_bag_folds = 5,num_bag_sets = 2
                              , **kwargs)
            else:
                predictor.fit(train_data=train_data[train_data[label] > float('-inf')]
                              , tuning_data = tuning_data
                              ,presets = 'medium_quality'
                              #,presets = 'best_quality'
                              #,num_bag_folds = 5,num_bag_sets = 2
                              , **kwargs)
            self.predictors[label] = predictor.path
            if save_metrics:
                self.eval_metrics[label] = predictor.eval_metric
        self.save()

    def predict(self, data, **kwargs):
        """ Returns DataFrame with label columns containing predictions for each label.

            Parameters
            ----------
            data : str or autogluon.tabular.TabularDataset or pd.DataFrame
                Data to make predictions for. If label columns are present in this data, they will be ignored. See documentation for `TabularPredictor.predict()`.
            kwargs :
                Arguments passed into the predict() call for each TabularPredictor.
        """
        return self._predict(data, as_proba=False, **kwargs)

    def predict_proba(self, data, **kwargs):
        """ Returns dict where each key is a label and the corresponding value is the `predict_proba()` output for just that label.

            Parameters
            ----------
            data : str or autogluon.tabular.TabularDataset or pd.DataFrame
                Data to make predictions for. See documentation for `TabularPredictor.predict()` and `TabularPredictor.predict_proba()`.
            kwargs :
                Arguments passed into the `predict_proba()` call for each TabularPredictor (also passed into a `predict()` call).
        """
        return self._predict(data, as_proba=True, **kwargs)

    def evaluate(self, data, **kwargs):
        """ Returns dict where each key is a label and the corresponding value is the `evaluate()` output for just that label.

            Parameters
            ----------
            data : str or autogluon.tabular.TabularDataset or pd.DataFrame
                Data to evalate predictions of all labels for, must contain all labels as columns. See documentation for `TabularPredictor.evaluate()`.
            kwargs :
                Arguments passed into the `evaluate()` call for each TabularPredictor (also passed into the `predict()` call).
        """
        data = self._get_data(data)
        eval_dict = {}
        for label in self.labels:
            print(f"Evaluating TabularPredictor for label: {label} ...")
            predictor = self.get_predictor(label)
            
            eval_dict[label] = predictor.evaluate(data[data[label] > float('-inf')], **kwargs)
            if self.consider_labels_correlation:
                data[label] = predictor.predict(data, **kwargs)
        return eval_dict

    def save(self):
        """ Save MultilabelPredictor to disk. """
        for label in self.labels:
            if not isinstance(self.predictors[label], str):
                self.predictors[label] = self.predictors[label].path
        save_pkl.save(path=self.path+self.multi_predictor_file, object=self)
        print(f"MultilabelPredictor saved to disk. Load with: MultilabelPredictor.load('{self.path}')")

    @classmethod
    def load(cls, path):
        """ Load MultilabelPredictor from disk `path` previously specified when creating this MultilabelPredictor. """
        path = os.path.expanduser(path)
        if path[-1] != os.path.sep:
            path = path + os.path.sep
        return load_pkl.load(path=path+cls.multi_predictor_file)

    def get_predictor(self, label):
        """ Returns TabularPredictor which is used to predict this label. """
        predictor = self.predictors[label]
        if isinstance(predictor, str):
            return TabularPredictor.load(path=predictor)
        return predictor

    def _get_data(self, data):
        if isinstance(data, str):
            return TabularDataset(data)
        return data.copy()

    def _predict(self, data, as_proba=False, **kwargs):
        data = self._get_data(data)
        if as_proba:
            predproba_dict = {}
        for i,label in enumerate(self.labels):
            print(f"Predicting with TabularPredictor for label: {label} ...{i / len(self.labels) * 100}%")
            predictor = self.get_predictor(label)
            if as_proba:
                predproba_dict[label] = predictor.predict_proba(data, as_multiclass=True, **kwargs)
            data[label] = predictor.predict(data, **kwargs)
        if not as_proba:
            return data[self.labels]
        else:
            return predproba_dict

In [3]:
#1 Load my ccl's ssGSEA signature
myCCLSignature = []
for name in ['sample.c2.cp.biocarta.gct',
             'sample.c2.cp.kegg.gct',
             'sample.c2.cp.pid.gct',
             'sample.c2.cp.reactome.gct',
             'sample.c2.cp.wiki.gct',
             'sample.c6.gct',
             'sample.hallmark.gct']:    
    with open(name, mode ='r')as file:
        csvFile = csv.reader(file)
        CCLSignature = list(csvFile)[2:]
        print(len(CCLSignature))
    for i, row in enumerate(CCLSignature):
        temp = CCLSignature[i][0].split('\t')
        if i > 0:
            CCLSignature[i] = [temp[0]] + [float(d) for d in temp[2:]]
        else:
            CCLSignature[i] = [temp[0]] + temp[2:]
    if not myCCLSignature:
        myCCLSignature += CCLSignature
    else:
        myCCLSignature += CCLSignature[1:]

293
187
197
1616
665
280
53


In [4]:
#2 Load CCLE ssGSEA signature
CCLECCLSignature = []
for name in ['ccle.c2.cp.biocarta.gct',
             'ccle.c2.cp.kegg.gct',
             'ccle.c2.cp.pid.gct',
             'ccle.c2.cp.reactome.gct',
             'ccle.c2.cp.wiki.gct',
             'ccle.c6.gct',
             'ccle.hallmark.gct']:
    with open(name, mode ='r')as file:
        csvFile = csv.reader(file)
        CCLSignature = list(csvFile)[2:]
        print(len(CCLSignature))
    for i, row in enumerate(CCLSignature):
        temp = CCLSignature[i][0].split('\t')
        CCLSignature[i] = [temp[0]] + temp[2:]
    if not CCLECCLSignature:
        CCLECCLSignature += CCLSignature
    else:
        CCLECCLSignature += CCLSignature[1:]

293
187
197
1616
665
280
53


In [5]:
#3 Load CTRP cclName to AUC map
cclToAUCdict = collections.defaultdict(list)
with open('CTRP_CCL_AUC.gct', mode ='r') as file:
    csvFile = csv.reader(file)
    CTRPCCLAUC = list(csvFile)
    CTRPCCLAUC = [''.join(sub).split('\t') for sub in CTRPCCLAUC]
    cclNames = CTRPCCLAUC[3][4:]

for i,cclName in enumerate(cclNames):
    cclToAUCdict[cclName] = [float( '-inf' if sub[4+i] == 'NaN' else sub[4+i]) for sub in CTRPCCLAUC[7:]]

In [6]:
#4 Load ccleID to ctrpName map
CCLEidToCTRPNameDict = collections.defaultdict(str)
CCLEidToDiseaseName = collections.defaultdict(str)
with open('sample_info.csv', mode ='r') as file:
    csvFile = csv.reader(file)
    mapInfos = list(csvFile)
    for mapInfo in mapInfos[1:]:
        CCLEidToCTRPNameDict[mapInfo[0]] = mapInfo[2]  
        CCLEidToDiseaseName[mapInfo[0]] = mapInfo[12]

In [7]:
def normalize(df):
    result = df.copy()
    for feature_name in df.columns:
        max_value = df[feature_name].max()
        min_value = df[feature_name].min()
        result[feature_name] = (df[feature_name] - min_value) / (max_value - min_value)
    return result

In [8]:
# prediction data 
predictData = pd.DataFrame(data = myCCLSignature).transpose()
new_header = predictData.iloc[0] 
predictData = predictData[1:] 
predictData.columns = new_header 
predictData = predictData.apply(pd.to_numeric, errors='ignore')
predictData = predictData.set_index(['Name'])
predictData = normalize(predictData)
predictData.head()

0                   BIOCARTA_GRANULOCYTES_PATHWAY  BIOCARTA_LYM_PATHWAY  \
Name                                                                      
THP1_d3_B.TPM                            0.991211              0.985279   
2D_1.TPM                                 0.160241              0.161473   
TRId7CWa.quant.TPM                       0.438166              0.443539   
H7.TPM                                   0.553921              0.562553   
THP1_d3_A.TPM                            0.992471              0.992554   

0                   BIOCARTA_BLYMPHOCYTE_PATHWAY  BIOCARTA_CARM_ER_PATHWAY  \
Name                                                                         
THP1_d3_B.TPM                           0.984154                  0.876359   
2D_1.TPM                                0.059402                  0.379321   
TRId7CWa.quant.TPM                      0.540397                  0.000000   
H7.TPM                                  0.428064                  1.000000   
THP1_d3_A.TPM                           0.973644                  0.795964   

0                   BIOCARTA_LAIR_PATHWAY  BIOCARTA_VDR_PATHWAY  \
Name                                                              
THP1_d3_B.TPM                    0.993570              0.595547   
2D_1.TPM                         0.045364              1.000000   
TRId7CWa.quant.TPM               0.506852              0.304020   
H7.TPM                           0.724494              0.403809   
THP1_d3_A.TPM                    0.999802              0.548292   

0                   BIOCARTA_MTA3_PATHWAY  BIOCARTA_GABA_PATHWAY  \
Name                                                               
THP1_d3_B.TPM                    0.475054               0.492397   
2D_1.TPM                         0.089837               0.554072   
TRId7CWa.quant.TPM               0.583516               0.429940   
H7.TPM                           0.852908               0.493875   
THP1_d3_A.TPM                    0.615737               0.447267   

0                   BIOCARTA_EGFR_SMRTE_PATHWAY  BIOCARTA_MONOCYTE_PATHWAY  \
Name                                                                         
THP1_d3_B.TPM                          0.594030                   0.986427   
2D_1.TPM                               0.363435                   0.187854   
TRId7CWa.quant.TPM                     1.000000                   0.700186   
H7.TPM                                 0.511236                   0.531963   
THP1_d3_A.TPM                          0.474747                   0.989311   

0                   ...  HALLMARK_COAGULATION  HALLMARK_IL2_STAT5_SIGNALING  \
Name                ...                                                       
THP1_d3_B.TPM       ...              0.675939                      0.809839   
2D_1.TPM            ...              0.025288                      0.065203   
TRId7CWa.quant.TPM  ...              0.927243                      0.736486   
H7.TPM              ...              0.822794                      0.816438   
THP1_d3_A.TPM       ...              0.691364                      0.826434   

0                   HALLMARK_BILE_ACID_METABOLISM  HALLMARK_PEROXISOME  \
Name                                                                     
THP1_d3_B.TPM                            0.680037             0.774811   
2D_1.TPM                                 0.221749             0.194506   
TRId7CWa.quant.TPM                       0.484722             0.130770   
H7.TPM                                   0.113695             0.248351   
THP1_d3_A.TPM                            0.710767             0.877729   

0                   HALLMARK_ALLOGRAFT_REJECTION  HALLMARK_SPERMATOGENESIS  \
Name                                                                         
THP1_d3_B.TPM                           0.928606                  0.793392   
2D_1.TPM                                0.019127                  0.555587   
TRId7CWa.quant.TPM                      0.436573

In [9]:
# Prepare train set
trainData = pd.DataFrame(data = CCLECCLSignature).transpose()
new_header = trainData.iloc[0] 
trainData = trainData[1:] 
trainData.columns = new_header 

In [10]:
# filter valid ID
validSet = set()
for name in trainData['Name']:
    if CCLEidToCTRPNameDict[name] in cclToAUCdict:
        validSet.add(name)
trainData = trainData.loc[trainData['Name'].isin(validSet)]
trainData = trainData.reset_index(drop = True)
trainData = trainData.set_index(['Name'])
trainData = trainData.apply(pd.to_numeric)
trainData = normalize(trainData)
trainData = trainData[trainData.index.map(lambda x: 'Brain Cancer' in CCLEidToDiseaseName[x])]
trainData.head()

0           BIOCARTA_GRANULOCYTES_PATHWAY  BIOCARTA_LYM_PATHWAY  \
Name                                                              
ACH-000570                       0.110241              0.291122   
ACH-000075                       0.441704              0.498651   
ACH-000269                       0.360292              0.542315   
ACH-000376                       0.240780              0.457245   
ACH-000368                       0.226606              0.501144   

0           BIOCARTA_BLYMPHOCYTE_PATHWAY  BIOCARTA_CARM_ER_PATHWAY  \
Name                                                                 
ACH-000570                      0.046545                  0.411979   
ACH-000075                      0.489649                  0.690755   
ACH-000269                      0.357031                  0.328689   
ACH-000376                      0.135034                  0.803859   
ACH-000368                      0.073657                  0.574459   

0           BIOCARTA_LAIR_PATHWAY  BIOCARTA_VDR_PATHWAY  \
Name                                                      
ACH-000570               0.243086              0.676126   
ACH-000075               0.501035              0.433048   
ACH-000269               0.419947              0.623150   
ACH-000376               0.441461              0.644449   
ACH-000368               0.459650              0.534463   

0           BIOCARTA_MTA3_PATHWAY  BIOCARTA_GABA_PATHWAY  \
Name                                                       
ACH-000570               0.511251               0.415892   
ACH-000075               0.549499               0.535556   
ACH-000269               0.471118               0.417255   
ACH-000376               0.590507               0.707571   
ACH-000368               0.542507               0.503628   

0           BIOCARTA_EGFR_SMRTE_PATHWAY  BIOCARTA_MONOCYTE_PATHWAY  ...  \
Name                                                                ...   
ACH-000570                     0.433882                   0.374186  ...   
ACH-000075                     0.482125                   0.491177  ...   
ACH-000269                     0.473060                   0.480172  ...   
ACH-000376                     0.555921                   0.496256  ...   
ACH-000368                     0.616213                   0.489169  ...   

0           HALLMARK_COAGULATION  HALLMARK_IL2_STAT5_SIGNALING  \
Name                                                             
ACH-000570              0.569109                      0.544746   
ACH-000075              0.699880                      0.729686   
ACH-000269              0.538858                      0.611223   
ACH-000376              0.643381                      0.631357   
ACH-000368              0.701306                      0.636327   

0           HALLMARK_BILE_ACID_METABOLISM  HALLMARK_PEROXISOME  \
Name                                                             
ACH-000570                       0.255964             0.425612   
ACH-000075                       0.201376             0.381000   
ACH-000269                       0.201457             0.380954   
ACH-000376                       0.284282             0.516030   
ACH-000368                       0.134946             0.380434   

0           HALLMARK_ALLOGRAFT_REJECTION  HALLMARK_SPERMATOGENESIS  \
Name                                                                 
ACH-000570                      0.222951                  0.370397   
ACH-000075                      0.421537                  0.462070   
ACH-000269                      0.406162                  0.472731   
ACH-000376                      0.386196                  0.568442   
ACH-000368                      0.358833                  0.510700   

0           HALLMARK_KRAS_SIGNALING  HALLMARK_KRAS_SIGNALING_UP  \
Name                                                              
ACH-000570                 0.762753                    0.687468   
ACH-000075                 0.848547                    0.718

In [11]:
if not all(trainData.columns == predictData.columns):
    raise Exception("Column do not match!")

In [12]:
#labels data
labelsDataOriginal = pd.DataFrame(columns = [sub[1] for sub in CTRPCCLAUC[7:]])
for name in trainData.index:
    labelsDataOriginal.loc[len(labelsDataOriginal.index)] = cclToAUCdict[CCLEidToCTRPNameDict[name]]
labelsDataOriginal = labelsDataOriginal.set_index(trainData.index)

In [13]:
#labelsDataOriginal.rename(columns={"neuronal differentiation inducer III": "neuronal_differentiation_inducer_III"}, inplace=True)

In [14]:
#add high priority at the begining. e.g dasatinib
labels = list(labelsDataOriginal.columns)

In [15]:
#constants
problem_types = ['regression'] 
eval_metrics = ['mean_squared_error']
time_limit = 60 * 60 * 24
tops = [100,300,600]

In [16]:
visited = set()
for entry in os.scandir(os.getcwd()):
    if entry.is_dir():
        visited.add(entry.name)

In [17]:
#import os

#brain_cancer_path = 'BrainCancer'
#os.makedirs(brain_cancer_path, exist_ok=True)

for label in labels:
    if label == "neuronal differentiation inducer III" or label in visited:
        continue
    visited.add(label)
    print(label)
    
    labelData = labelsDataOriginal[[label]]    
    trainDataSet = pd.concat([trainData, labelData], axis = 1)
    
    #label_path = os.path.join(brain_cancer_path, label)
    #os.makedirs(label_path, exist_ok=True)
   
    #first time training 
    save_path = label + '/' + 'GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_' + label 
    #save_path = os.path.join(label_path, 'GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_' + label)
    multi_predictor = MultilabelPredictor(labels=[label], problem_types=problem_types, eval_metrics=eval_metrics, path=save_path)
    multi_predictor.fit(trainDataSet, time_limit=time_limit)
    
    #multi_predictor = MultilabelPredictor.load(save_path)
    result = multi_predictor.predict(predictData)
    #result_csv_path = os.path.join(label_path, 'GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Result_' + label + '.csv')
    #result.to_csv(result_csv_path)
    result.to_csv(label + '/' + 'GlioML_predictDrugAUC_Full_Feature_Medium_Quality_Result_' + label+ '.csv')

Presets specified: ['medium_quality']
Beginning AutoGluon training ... Time limit = 86400s
AutoGluon will save models to "zebularine/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_zebularine\Predictor_zebularine\"
AutoGluon Version:  0.8.0
Python Version:     3.9.0
Operating System:   Windows
Platform Machine:   AMD64
Platform Version:   10.0.22000
Disk Space Avail:   643.25 GB / 785.12 GB (81.9%)
Train Data Rows:    46
Train Data Columns: 3284
Label Column: zebularine
Preprocessing data ...
Using Feature Generators to preprocess the data ...
Fitting AutoMLPipelineFeatureGenerator...
	Available Memory:                    56287.07 MB
	Train Data (Original)  Memory Usage: 1.21 MB (0.0% of available memory)
	Inferring data type of each feature based on column values. Set feature_metadata_in to manually specify special dtypes of the features.


zebularine
Fitting TabularPredictor for label: zebularine ...0.0%
3.332694371541341e-05 minutes


	Stage 1 Generators:
		Fitting AsTypeFeatureGenerator...
	Stage 2 Generators:
		Fitting FillNaFeatureGenerator...
	Stage 3 Generators:
		Fitting IdentityFeatureGenerator...
	Stage 4 Generators:
		Fitting DropUniqueFeatureGenerator...
	Stage 5 Generators:
		Fitting DropDuplicatesFeatureGenerator...
	Unused Original Features (Count: 5): ['WP_INSULIN_SIGNALING_IN_ADIPOCYTES_DIABETIC_CONDITION', 'WP_CELLS_AND_MOLECULES_INVOLVED_IN_LOCAL_ACUTE_INFLAMMATORY_RESPONSE', 'WP_PATHOGENIC_ESCHERICHIA_COLI_INFECTION', 'WP_ARRHYTHMOGENIC_RIGHT_VENTRICULAR_CARDIOMYOPATHY', 'WP_ENDOCHONDRAL_OSSIFICATION']
		These features were not used to generate any of the output features. Add a feature generator compatible with these features to utilize them.
		Features can also be unused if they carry very little information, such as being categorical but having almost entirely unique values or being duplicates of other features.
		These features do not need to be present at inference time.
		('float', []) : 5 | [

MultilabelPredictor saved to disk. Load with: MultilabelPredictor.load('zebularine/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_zebularine\')
Predicting with TabularPredictor for label: zebularine ...0.0%


Presets specified: ['medium_quality']
Beginning AutoGluon training ... Time limit = 86400s
AutoGluon will save models to "azacitidine/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_azacitidine\Predictor_azacitidine\"
AutoGluon Version:  0.8.0
Python Version:     3.9.0
Operating System:   Windows
Platform Machine:   AMD64
Platform Version:   10.0.22000
Disk Space Avail:   643.23 GB / 785.12 GB (81.9%)
Train Data Rows:    45
Train Data Columns: 3284
Label Column: azacitidine
Preprocessing data ...
Using Feature Generators to preprocess the data ...
Fitting AutoMLPipelineFeatureGenerator...


...

Fitting model: LightGBMLarge ... Training model for up to 86380.15s of the 86380.1s of remaining time.
	-0.246	 = Validation score   (-mean_squared_error)
	0.7s	 = Training   runtime
	0.01s	 = Validation runtime
Fitting model: WeightedEnsemble_L2 ... Training model for up to 8639.45s of the 86379.25s of remaining time.
	-0.0042	 = Validation score   (-mean_squared_error)
	0.16s	 = Training   runtime
	0.0s	 = Validation runtime
AutoGluon training complete, total runtime = 20.94s ... Best model: "WeightedEnsemble_L2"
TabularPredictor saved. To load, use: predictor = TabularPredictor.load("SR8278/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_SR8278\Predictor_SR8278\")
Presets specified: ['medium_quality']
Beginning AutoGluon training ... Time limit = 86400s
AutoGluon will save models to "GSK-J4/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_GSK-J4\Predictor_GSK-J4\"
AutoGluon Version:  0.8.0
Python Version:     3.9.0
Operating System:   Windows
P

MultilabelPredictor saved to disk. Load with: MultilabelPredictor.load('SR8278/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_SR8278\')
Predicting with TabularPredictor for label: SR8278 ...0.0%
GSK-J4
Fitting TabularPredictor for label: GSK-J4 ...0.0%
1.666545867919922e-05 minutes


	Available Memory:                    57218.01 MB
	Train Data (Original)  Memory Usage: 0.16 MB (0.0% of available memory)
	Inferring data type of each feature based on column values. Set feature_metadata_in to manually specify special dtypes of the features.
	Stage 1 Generators:
		Fitting AsTypeFeatureGenerator...
	Stage 2 Generators:
		Fitting FillNaFeatureGenerator...
	Stage 3 Generators:
		Fitting IdentityFeatureGenerator...
	Stage 4 Generators:
		Fitting DropUniqueFeatureGenerator...
	Stage 5 Generators:
		Fitting DropDuplicatesFeatureGenerator...
	Unused Original Features (Count: 5): ['WP_INSULIN_SIGNALING_IN_ADIPOCYTES_DIABETIC_CONDITION', 'WP_CELLS_AND_MOLECULES_INVOLVED_IN_LOCAL_ACUTE_INFLAMMATORY_RESPONSE', 'WP_PATHOGENIC_ESCHERICHIA_COLI_INFECTION', 'WP_ARRHYTHMOGENIC_RIGHT_VENTRICULAR_CARDIOMYOPATHY', 'WP_ENDOCHONDRAL_OSSIFICATION']
		These features were not used to generate any of the output features. Add a feature generator compatible with these features to utilize them.


Fitting model: LightGBMLarge ... Training model for up to 86380.75s of the 86380.7s of remaining time.
	-2.4115	 = Validation score   (-mean_squared_error)
	0.71s	 = Training   runtime
	0.01s	 = Validation runtime
Fitting model: WeightedEnsemble_L2 ... Training model for up to 8639.44s of the 86379.83s of remaining time.
	-2.2701	 = Validation score   (-mean_squared_error)
	0.16s	 = Training   runtime
	0.0s	 = Validation runtime
AutoGluon training complete, total runtime = 20.37s ... Best model: "WeightedEnsemble_L2"
TabularPredictor saved. To load, use: predictor = TabularPredictor.load("GSK-J4/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_GSK-J4\Predictor_GSK-J4\")


MultilabelPredictor saved to disk. Load with: MultilabelPredictor.load('GSK-J4/GlioML_BrainCancer_predictDrugAUC_Full_Feature_Medium_Quality_Model_GSK-J4\')
Predicting with TabularPredictor for label: GSK-J4 ...0.0%
